In [1]:
!pip install gradio_client

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 318.7/318.7 kB 3.4 MB/s eta 0:00:00a 0:00:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 417.5/417.5 kB 11.2 MB/s eta 0:00:00


# PINDER inference and evaluation template API examples

## Run inference via predict endpoint

In [10]:
from gradio_client import Client, handle_file
from pathlib import Path

uri = "https://danielkovtun-pinder-inference-template.hf.space/"
# If running docker container locally
dev_uri = "http://localhost:7860/"
client = Client(uri)
result = client.predict(
    receptor_pdb=handle_file("./3g9w_R.pdb"),
    ligand_pdb=handle_file("./3g9w_L.pdb"),
    receptor_fasta=None, # optional in this implementation
    ligand_fasta=None,
    api_name="/predict"
)
output_pdb, runtime = Path(result[0]), result[1]
print(output_pdb, runtime)


Loaded as API: https://danielkovtun-pinder-inference-template.hf.space/ ✔
/private/var/folders/tt/x223wxwj6dzg3vjjgc_6y5bm0000gn/T/gradio/0cda59c2805986a9e5956ed00cb552b3c86f05915da91e6e14a0a31b962e664b/3g9w_R--3g9w_L.pdb 1.2273471355438232


In [11]:
import shutil

local_dir = Path("./pinder-inference-outputs")
local_dir.mkdir(exist_ok=True, parents=True)

output_pdb = Path(shutil.copy(output_pdb, local_dir))
output_pdb, output_pdb.is_file() 



(PosixPath('pinder-inference-outputs/3g9w_R--3g9w_L.pdb'), True)

## Fetch evaluation metrics via evaluate endpoint

In [13]:
client = Client(uri)
result = client.predict(
    system_id="3g9w__A1_Q71LX4--3g9w__D1_P05556",
    prediction_pdb=handle_file("3g9w_R--3g9w_L.pdb"),
    api_name="/evaluate"
)
metrics, pred_native, runtime = result
metrics

Loaded as API: http://localhost:7860/ ✔


{'headers': ['system', 'L_rms', 'I_rms', 'F_nat', 'DOCKQ', 'CAPRI_class'],
 'data': [['3g9w__A1_Q71LX4--3g9w__D1_P05556',
   34.781349182128906,
   15.405366897583008,
   0.0,
   0.021916405918697517,
   'Incorrect']],
 'metadata': None}

In [14]:
import pandas as pd

metric_df = pd.DataFrame(metrics["data"], columns=metrics["headers"])
metric_df

system      L_rms      I_rms  F_nat     DOCKQ  \
0  3g9w__A1_Q71LX4--3g9w__D1_P05556  34.781349  15.405367    0.0  0.021916   

  CAPRI_class  
0   Incorrect